# **Kaggle Project**
## **Irem Nesli Erez & Ezgi Siir Kibris**

In [1]:
# This section of the code is added by default.

# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
# Import the necessary packages

import nltk #language processing
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet
from nltk.corpus import stopwords

import re
import emoji

from sklearn.feature_extraction.text import CountVectorizer #for bag of words

import gensim
from gensim.models import Word2Vec

from sklearn import preprocessing
from sklearn.decomposition import PCA

import matplotlib.pyplot as plt
import matplotlib as mpl
import seaborn as sns

from scipy import interpolate
from scipy.spatial import ConvexHull

from sklearn.manifold import SpectralEmbedding

from sklearn.manifold import TSNE

from sklearn.linear_model import LogisticRegressionCV

path = '/Users/nesli/Desktop/SPRING 2022/DSCC 465/Kaggle_istanbul/'
os.chdir(path)

import random
random.seed(465) #seed

## Read the data

In [3]:
# Training data set
data_train = pd.read_csv('congressional_tweet_training_data.csv')
data_train

favorite_count                                          full_text  \
0                    0  b"RT @KUSINews: One of our longtime viewers wa...   
1                  258  b"Today I'm urging the @CDCgov to immediately ...   
2                    0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                    9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                    3  b'Pleased to support @amergateways at their Ju...   
...                ...                                                ...   
592798               3  b'This time, it focused on careers in #publics...   
592799               5  b'.#StormyDaniels, #MichaelWolfe, #JamesComey ...   
592800              33  b'@NRDems The American people deserve the trut...   
592801               4  b'Only 2 weeks left to submit your #app to the...   
592802             155  b'The #MuslimBan remains as un-American and of...   

                                     hashtags  retweet_count    year party_id  
0                                        KUSI             10  2017.0        R  
1                                 Coronavirus            111  2020.0        R  
2                                        MO03              2  2014.0        R  
3                        TeamUSA WorldJuniors              3  2017.0        R  
4                      ImmigrantHeritageMonth              3  2019.0        D  
...                                       ...            ...     ...      ...  
592798             publicservice publicsafety              0  2017.0        R  
592799  StormyDaniels MichaelWolfe JamesComey              1  2018.0        R  
592800                    CultureOfCorruption             14  2020.0        D  
592801  app copolitics CAC16 HouseOfCode co06              3  2016.0        R  
592802                              MuslimBan             48  2020.0        D  

[592803 rows x 6 columns]

In [4]:
# Test data set
data_test = pd.read_csv('congressional_tweet_test_data.csv')
data_test #party is set to D by default

Id  favorite_count  \
0            0              70   
1            1              27   
2            2              49   
3            3              14   
4            4              13   
...        ...             ...   
264995  264995             516   
264996  264996               0   
264997  264997               1   
264998  264998            2174   
264999  264999               6   

                                                full_text  \
0       b'#TaxReform improved the playing field for Am...   
1       b'This #NativeWomensEqualPay Day, we recommit ...   
2       b"\xe2\x80\x9cI became convinced that our gene...   
3       b'During #NationalAdoptionMonth, we honor the ...   
4       b'Happy #AirborneDay to our @USArmy paratroope...   
...                                                   ...   
264995  b'We need to #ExtendCHIP before a single child...   
264996  b"Our #ObamaCare investigation continued today...   
264997  b'Congratulations to the new #MissTeenUSA Loga...   
264998  b'Speaking of dishonesty. Nothing like being c...   
264999  b'In honor of #ConstitutionDay, we remember th...   

                             hashtags  retweet_count    year party  
0                           TaxReform             13  2018.0     D  
1                NativeWomensEqualPay             11     NaN     D  
2          MeToo ShatteringTheSilence             24  2017.0     D  
3               NationalAdoptionMonth              2  2019.0     D  
4       AirborneDay AirborneAllTheWay              7  2018.0     D  
...                               ...            ...     ...   ...  
264995                     ExtendCHIP            223  2017.0     D  
264996                      ObamaCare              3  2013.0     D  
264997                 MissTeenUSA CT              4  2012.0     D  
264998                          mosen           1168  2018.0     D  
264999                ConstitutionDay              3  2015.0     D  

[265000 rows x 7 columns]

In [5]:
# Check for number of rows that have NaN  [4]
data_train.isnull().any(axis=1).sum()

18712

In [6]:
data_train.isnull().any(axis=1).sum()/len(data_train)

0.03156529234838555

In [7]:
# Check for number of rows that have NaN [4]
data_test.isnull().any(axis=1).sum()

8347

In [8]:
data_test.isnull().any(axis=1).sum()/len(data_test)

0.03149811320754717

Since it is only $3\%$, we can drop the rows with "NaN" values. 

In [9]:
data_train=data_train.dropna()

In [10]:
data_test=data_test.dropna()

In [11]:
#Fix the indexing after dropping some rows [3]
data_train.reset_index(drop=True, inplace=True)

In [12]:
data_test.reset_index(drop=True, inplace=True)

In [13]:
data_train

favorite_count                                          full_text  \
0                    0  b"RT @KUSINews: One of our longtime viewers wa...   
1                  258  b"Today I'm urging the @CDCgov to immediately ...   
2                    0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                    9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                    3  b'Pleased to support @amergateways at their Ju...   
...                ...                                                ...   
574086               3  b'This time, it focused on careers in #publics...   
574087               5  b'.#StormyDaniels, #MichaelWolfe, #JamesComey ...   
574088              33  b'@NRDems The American people deserve the trut...   
574089               4  b'Only 2 weeks left to submit your #app to the...   
574090             155  b'The #MuslimBan remains as un-American and of...   

                                     hashtags  retweet_count    year party_id  
0                                        KUSI             10  2017.0        R  
1                                 Coronavirus            111  2020.0        R  
2                                        MO03              2  2014.0        R  
3                        TeamUSA WorldJuniors              3  2017.0        R  
4                      ImmigrantHeritageMonth              3  2019.0        D  
...                                       ...            ...     ...      ...  
574086             publicservice publicsafety              0  2017.0        R  
574087  StormyDaniels MichaelWolfe JamesComey              1  2018.0        R  
574088                    CultureOfCorruption             14  2020.0        D  
574089  app copolitics CAC16 HouseOfCode co06              3  2016.0        R  
574090                              MuslimBan             48  2020.0        D  

[574091 rows x 6 columns]

In [14]:
data_test

Id  favorite_count  \
0            0              70   
1            2              49   
2            3              14   
3            4              13   
4            5              73   
...        ...             ...   
256648  264995             516   
256649  264996               0   
256650  264997               1   
256651  264998            2174   
256652  264999               6   

                                                full_text  \
0       b'#TaxReform improved the playing field for Am...   
1       b"\xe2\x80\x9cI became convinced that our gene...   
2       b'During #NationalAdoptionMonth, we honor the ...   
3       b'Happy #AirborneDay to our @USArmy paratroope...   
4       b"Proud to join 200+ colleagues in SCOTUS amic...   
...                                                   ...   
256648  b'We need to #ExtendCHIP before a single child...   
256649  b"Our #ObamaCare investigation continued today...   
256650  b'Congratulations to the new #MissTeenUSA Loga...   
256651  b'Speaking of dishonesty. Nothing like being c...   
256652  b'In honor of #ConstitutionDay, we remember th...   

                             hashtags  retweet_count    year party  
0                           TaxReform             13  2018.0     D  
1          MeToo ShatteringTheSilence             24  2017.0     D  
2               NationalAdoptionMonth              2  2019.0     D  
3       AirborneDay AirborneAllTheWay              7  2018.0     D  
4                                LGBT             13  2017.0     D  
...                               ...            ...     ...   ...  
256648                     ExtendCHIP            223  2017.0     D  
256649                      ObamaCare              3  2013.0     D  
256650                 MissTeenUSA CT              4  2012.0     D  
256651                          mosen           1168  2018.0     D  
256652                ConstitutionDay              3  2015.0     D  

[256653 rows x 7 columns]

## Kodu hizlandirmak icin

In [15]:
data_train[0:100]

favorite_count                                          full_text  \
0                0  b"RT @KUSINews: One of our longtime viewers wa...   
1              258  b"Today I'm urging the @CDCgov to immediately ...   
2                0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                3  b'Pleased to support @amergateways at their Ju...   
..             ...                                                ...   
95            1720  b'Tragedy in my #CA15. Hold these grieving fam...   
96               1  b'\xf0\x9f\x9a\x9b\xf0\x9f\x9b\xa3 Had a great...   
97              28  b'This morning, I had a good, constructive dis...   
98               5  b"Met w/local leaders at @FoLARtweets Noche de...   
99               1  b'There are 4 weeks left to submit your apps a...   

                    hashtags  retweet_count    year party_id  
0                       KUSI             10  2017.0        R  
1                Coronavirus            111  2020.0        R  
2                       MO03              2  2014.0        R  
3       TeamUSA WorldJuniors              3  2017.0        R  
4     ImmigrantHeritageMonth              3  2019.0        D  
..                       ...            ...     ...      ...  
95                      CA15            176  2019.0        D  
96  Burlington WorkingforWA2              2  2019.0        D  
97       Cambridge taxreform              8  2018.0        R  
98                   LARiver              2  2017.0        D  
99                     CAC16              1  2016.0        D  

[100 rows x 6 columns]

In [16]:
data_train=data_train[0:100]

In [17]:
data_test=data_test[0:100]

## Data Pre-processing

First, preprocess the full_text feature of the tweets for both test and the train data sets.

In [18]:
#add a numerical column for the class
data_train['party_class']=[0] * len(data_train)

for i in np.arange(len(data_train)):
    #Because D is the default
    if data_train['party_id'][i]=='D':
        data_train['party_class'][i]=0
    else:
        data_train['party_class'][i]=1

/var/folders/dt/96l3vfgd54s0dlvms03s3z400000gn/T/ipykernel_16463/457533936.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_train['party_class']=[0] * len(data_train)
/var/folders/dt/96l3vfgd54s0dlvms03s3z400000gn/T/ipykernel_16463/457533936.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_train['party_class'][i]=1
/var/folders/dt/96l3vfgd54s0dlvms03s3z400000gn/T/ipykernel_16463/457533936.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org

In [19]:
#Code from HW4 CITE IT!

In [20]:
# Start by cleaning the full text of the tweets 
data_train.dropna(subset=['full_text'],inplace=True) #First, I drop the rows with NA in the text column
data_train

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/pandas/util/_decorators.py:311: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return func(*args, **kwargs)


favorite_count                                          full_text  \
0                0  b"RT @KUSINews: One of our longtime viewers wa...   
1              258  b"Today I'm urging the @CDCgov to immediately ...   
2                0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                3  b'Pleased to support @amergateways at their Ju...   
..             ...                                                ...   
95            1720  b'Tragedy in my #CA15. Hold these grieving fam...   
96               1  b'\xf0\x9f\x9a\x9b\xf0\x9f\x9b\xa3 Had a great...   
97              28  b'This morning, I had a good, constructive dis...   
98               5  b"Met w/local leaders at @FoLARtweets Noche de...   
99               1  b'There are 4 weeks left to submit your apps a...   

                    hashtags  retweet_count    year party_id  party_class  
0                       KUSI             10  2017.0        R            1  
1                Coronavirus            111  2020.0        R            1  
2                       MO03              2  2014.0        R            1  
3       TeamUSA WorldJuniors              3  2017.0        R            1  
4     ImmigrantHeritageMonth              3  2019.0        D            0  
..                       ...            ...     ...      ...          ...  
95                      CA15            176  2019.0        D            0  
96  Burlington WorkingforWA2              2  2019.0        D            0  
97       Cambridge taxreform              8  2018.0        R            1  
98                   LARiver              2  2017.0        D            0  
99                     CAC16              1  2016.0        D            0  

[100 rows x 7 columns]

In [21]:
data_train=data_train.reset_index(drop=True) #to fix the indices

In [22]:
#Tokenize
tokens_list=list()
for i in np.arange(len(data_train)):
    tokens_list.append(nltk.word_tokenize(str(data_train['full_text'][i])))

In [23]:
tagged_tokens=list()
for i in np.arange(len(tokens_list)):
    tagged_tokens.append(nltk.pos_tag(tokens_list[i]))

In [24]:
def get_wordnet_pos(treebank_tag): #Following from [16]

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return None # for easy if-statement 

In [25]:
lemmatizer = WordNetLemmatizer()

In [26]:
lemma_list=list()

for i in np.arange(len(tagged_tokens)):
    lemma=list()
    for j in np.arange(len(tagged_tokens[i])):
        
        token=tagged_tokens[i][j][0] 
        tag=tagged_tokens[i][j][1]
        
        wntag = get_wordnet_pos(tag)
        if wntag is None:           #do not supply tag in case of None
            lemma.append(lemmatizer.lemmatize(token))
        else:
            lemma.append(lemmatizer.lemmatize(token, pos=wntag))
    lemma_list.append(lemma)
        

In [27]:
len(lemma_list)

100

In [28]:
# Before removing elements from the string, make all of them lowercase
filtered_lower=list()
for i in np.arange(len(lemma_list)):
    lowered=list()
    for j in np.arange(len(lemma_list[i])):
        lowered.append(lemma_list[i][j].lower())
    filtered_lower.append(lowered)  

In [29]:
# Now to remove stop words like 'the', 'a', 'and' 
stop_words = set(stopwords.words('english'))

In [30]:
filtered_list=list()
for i in np.arange(len(filtered_lower)):
    filtered_list.append([w for w in filtered_lower[i] if not w.lower() in stop_words])

In [31]:
len(filtered_list)

100

In [32]:
# Remove numbers, words <2 characters, punctuation, links and emojis 

def emoji_free_text(text): # From [9] 
    return emoji.get_emoji_regexp().sub(r'', text)

In [33]:
filtered_elements=list()

for i in np.arange(len(filtered_list)):
    filter_element=list()
    for j in np.arange(len(filtered_list[i])):
        
        element=re.sub(r'\d+', '',filtered_list[i][j])          # Remove numbers
        element=re.sub(r'\b\w{1}\b', '', element)               # Remove <2 characters
        element=re.sub(r'[^\w\s]', '', element)                 # Remove punctuation
        element=re.sub(r'http\S+', '', element)                 # Remove links
        #element=re.sub('/[\u{1f300}-\u{1f5ff}]/', '', element) # Remove symbols
        #element=re.sub('/[\u{1f600}-\u{1f64f}]/','', element)  # Remove emoticons
        emoji_free_text(element)
        
        filter_element.append(element)
    filtered_elements.append(filter_element)   

In [34]:
# Combine the elements back to form sentences
text_clean_list=list()
s=' '

for i in np.arange(len(filtered_elements)):
    text_clean_list.append(s.join(filtered_elements[i]))

In [35]:
len(text_clean_list)

100

In [36]:
# Add a new column of 'text_clean'
data_train.insert(7, "text_clean", text_clean_list)

In [37]:
data_train.head()

favorite_count                                          full_text  \
0               0  b"RT @KUSINews: One of our longtime viewers wa...   
1             258  b"Today I'm urging the @CDCgov to immediately ...   
2               0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3               9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4               3  b'Pleased to support @amergateways at their Ju...   

                 hashtags  retweet_count    year party_id  party_class  \
0                    KUSI             10  2017.0        R            1   
1             Coronavirus            111  2020.0        R            1   
2                    MO03              2  2014.0        R            1   
3    TeamUSA WorldJuniors              3  2017.0        R            1   
4  ImmigrantHeritageMonth              3  2019.0        D            0   

                                          text_clean  
0    rt  kusinews  one longtime viewer congressma...  
1    today  urge  cdcgov immediately launch  phon...  
2  tomorrow   mo senior graduate calvary lutheran...  
3  congrats  teamusa canton native  jgreenway win...  
4  pleased support  amergateways june fiesta  hon...

In [38]:
# Repeat the same for the test data

# Start by cleaning the full text of the tweets 
data_test.dropna(subset=['full_text'],inplace=True) #First, I drop the rows with NA in the text column
data_test

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/pandas/util/_decorators.py:311: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return func(*args, **kwargs)


Id  favorite_count                                          full_text  \
0     0              70  b'#TaxReform improved the playing field for Am...   
1     2              49  b"\xe2\x80\x9cI became convinced that our gene...   
2     3              14  b'During #NationalAdoptionMonth, we honor the ...   
3     4              13  b'Happy #AirborneDay to our @USArmy paratroope...   
4     5              73  b"Proud to join 200+ colleagues in SCOTUS amic...   
..  ...             ...                                                ...   
95  103               2  b"Joining the CO Delegation in support of Gov ...   
96  104               7  b'.@SwiftTransport merger w/ @DriveKnight is g...   
97  105               7  b'Had a great time @ the Sentara Heart Hospita...   
98  106               3  b"Thank you to @arnoldporter for inviting me t...   
99  107               8  b'ICYMI: Rep. Tulsi Gabbard joins congressiona...   

                         hashtags  retweet_count    year party  
0                       TaxReform             13  2018.0     D  
1      MeToo ShatteringTheSilence             24  2017.0     D  
2           NationalAdoptionMonth              2  2019.0     D  
3   AirborneDay AirborneAllTheWay              7  2018.0     D  
4                            LGBT             13  2017.0     D  
..                            ...            ...     ...   ...  
95                     copolitics              2  2015.0     D  
96                             AZ              6  2017.0     D  
97                      OurHearts              3  2020.0     D  
98                       COVID_19              2  2020.0     D  
99                           STEM              6  2015.0     D  

[100 rows x 7 columns]

In [39]:
data_test=data_test.reset_index(drop=True) #to fix the indices

In [40]:
#Tokenize
tokens_list=list()
for i in np.arange(len(data_test)):
    tokens_list.append(nltk.word_tokenize(str(data_test['full_text'][i])))

In [41]:
tagged_tokens=list()
for i in np.arange(len(tokens_list)):
    tagged_tokens.append(nltk.pos_tag(tokens_list[i]))

In [42]:
def get_wordnet_pos(treebank_tag): #Following from [16]

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return None # for easy if-statement 

In [43]:
lemmatizer = WordNetLemmatizer()

In [44]:
lemma_list=list()

for i in np.arange(len(tagged_tokens)):
    lemma=list()
    for j in np.arange(len(tagged_tokens[i])):
        
        token=tagged_tokens[i][j][0] 
        tag=tagged_tokens[i][j][1]
        
        wntag = get_wordnet_pos(tag)
        if wntag is None:           #do not supply tag in case of None
            lemma.append(lemmatizer.lemmatize(token))
        else:
            lemma.append(lemmatizer.lemmatize(token, pos=wntag))
    lemma_list.append(lemma)
        

In [45]:
len(lemma_list)

100

In [46]:
# Before removing elements from the string, make all of them lowercase
filtered_lower=list()
for i in np.arange(len(lemma_list)):
    lowered=list()
    for j in np.arange(len(lemma_list[i])):
        lowered.append(lemma_list[i][j].lower())
    filtered_lower.append(lowered)  

In [47]:
# Now to remove stop words like 'the', 'a', 'and' 
stop_words = set(stopwords.words('english'))

In [48]:
filtered_list=list()
for i in np.arange(len(filtered_lower)):
    filtered_list.append([w for w in filtered_lower[i] if not w.lower() in stop_words])

In [49]:
len(filtered_list)

100

In [50]:
# Remove numbers, words <2 characters, punctuation, links and emojis 

def emoji_free_text(text): # From [9]
    return emoji.get_emoji_regexp().sub(r'', text)

In [51]:
filtered_elements=list()

for i in np.arange(len(filtered_list)):
    filter_element=list()
    for j in np.arange(len(filtered_list[i])):
        
        element=re.sub(r'\d+', '',filtered_list[i][j])          # Remove numbers
        element=re.sub(r'\b\w{1}\b', '', element)               # Remove <2 characters
        element=re.sub(r'[^\w\s]', '', element)                 # Remove punctuation
        element=re.sub(r'http\S+', '', element)                 # Remove links
        #element=re.sub('/[\u{1f300}-\u{1f5ff}]/', '', element) # Remove symbols
        #element=re.sub('/[\u{1f600}-\u{1f64f}]/','', element)  # Remove emoticons
        emoji_free_text(element)
        
        filter_element.append(element)
    filtered_elements.append(filter_element)   

In [52]:
# Combine the elements back to form sentences
text_clean_list=list()
s=' '

for i in np.arange(len(filtered_elements)):
    text_clean_list.append(s.join(filtered_elements[i]))

In [53]:
len(text_clean_list)

100

In [54]:
# Add a new column of 'text_clean'
data_test.insert(7, "text_clean", text_clean_list)

In [55]:
data_test.head()

Id  favorite_count                                          full_text  \
0   0              70  b'#TaxReform improved the playing field for Am...   
1   2              49  b"\xe2\x80\x9cI became convinced that our gene...   
2   3              14  b'During #NationalAdoptionMonth, we honor the ...   
3   4              13  b'Happy #AirborneDay to our @USArmy paratroope...   
4   5              73  b"Proud to join 200+ colleagues in SCOTUS amic...   

                        hashtags  retweet_count    year party  \
0                      TaxReform             13  2018.0     D   
1     MeToo ShatteringTheSilence             24  2017.0     D   
2          NationalAdoptionMonth              2  2019.0     D   
3  AirborneDay AirborneAllTheWay              7  2018.0     D   
4                           LGBT             13  2017.0     D   

                                          text_clean  
0     taxreform improve playing field american wo...  
1    xexci become convinced generation silence ma...  
2  during  nationaladoptionmonth  honor adoptive ...  
3  happy  airborneday  usarmy paratrooper veteran...  
4    proud join  colleague scotus amicus brief ar...

## How to deal with shortened words like rt?

We could create a dictionary for that, but we assume that the senators(?) use English properly.

## Vectorize the data

Now for vectorization, we can use different techniques. Try two different methods:

1. Bag of words
2. Word2vec

We will not try TF-IDF because it is rather beneficial for long text data.

Considering the fact that the bag of words method includes each unique word in the text as a dimension, it is better to apply vectorization on the merged data set that contains both the test and the training sets.

But we would like the same vectorization to happen for all of the data.

In [56]:
data=pd.concat([data_train,data_test], ignore_index=True)

In [57]:
data

favorite_count                                          full_text  \
0                 0  b"RT @KUSINews: One of our longtime viewers wa...   
1               258  b"Today I'm urging the @CDCgov to immediately ...   
2                 0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                 9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                 3  b'Pleased to support @amergateways at their Ju...   
..              ...                                                ...   
195               2  b"Joining the CO Delegation in support of Gov ...   
196               7  b'.@SwiftTransport merger w/ @DriveKnight is g...   
197               7  b'Had a great time @ the Sentara Heart Hospita...   
198               3  b"Thank you to @arnoldporter for inviting me t...   
199               8  b'ICYMI: Rep. Tulsi Gabbard joins congressiona...   

                   hashtags  retweet_count    year party_id  party_class  \
0                      KUSI             10  2017.0        R          1.0   
1               Coronavirus            111  2020.0        R          1.0   
2                      MO03              2  2014.0        R          1.0   
3      TeamUSA WorldJuniors              3  2017.0        R          1.0   
4    ImmigrantHeritageMonth              3  2019.0        D          0.0   
..                      ...            ...     ...      ...          ...   
195              copolitics              2  2015.0      NaN          NaN   
196                      AZ              6  2017.0      NaN          NaN   
197               OurHearts              3  2020.0      NaN          NaN   
198                COVID_19              2  2020.0      NaN          NaN   
199                    STEM              6  2015.0      NaN          NaN   

                                            text_clean     Id party  
0      rt  kusinews  one longtime viewer congressma...    NaN   NaN  
1      today  urge  cdcgov immediately launch  phon...    NaN   NaN  
2    tomorrow   mo senior graduate calvary lutheran...    NaN   NaN  
3    congrats  teamusa canton native  jgreenway win...    NaN   NaN  
4    pleased support  amergateways june fiesta  hon...    NaN   NaN  
..                                                 ...    ...   ...  
195    joining co delegation support gov hickenloop...  103.0     D  
196      swifttransport merger   driveknight great ...  104.0     D  
197  had great time  sentara heart hospitalxexs ann...  105.0     D  
198    thank  arnoldporter invite join policymakers...  106.0     D  
199  icymi  rep tulsi gabbard join congressional le...  107.0     D  

[200 rows x 10 columns]

In [58]:
# Bag of words
# Following from [1]
vectorizer = CountVectorizer()

text_bow = vectorizer.fit_transform(data['text_clean'])
text_bow_df = pd.DataFrame(text_bow.toarray(),columns=vectorizer.get_feature_names())

In [59]:
text_bow_df

abcnews  able  abortion  abrams  absolutely  aca  access  accessibility  \
0          0     0         0       0           0    0       0              0   
1          0     0         0       0           0    0       0              0   
2          0     0         0       0           0    0       0              0   
3          0     0         0       0           0    0       0              0   
4          0     0         0       0           0    0       0              0   
..       ...   ...       ...     ...         ...  ...     ...            ...   
195        0     0         0       0           0    0       0              0   
196        0     0         0       0           0    0       0              0   
197        0     0         0       0           0    0       0              0   
198        0     0         0       0           0    0       0              0   
199        0     0         0       0           0    0       0              0   

     accomplish  accordingly  ...  yesterday  yet  yorkers  young  youth  \
0             0            0  ...          0    0        0      0      0   
1             0            0  ...          0    0        0      0      0   
2             0            0  ...          0    0        0      0      0   
3             0            0  ...          0    0        0      0      0   
4             0            0  ...          0    0        0      0      0   
..          ...          ...  ...        ...  ...      ...    ...    ...   
195           0            0  ...          0    0        0      0      0   
196           0            0  ...          0    0        0      0      0   
197           0            0  ...          0    0        0      0      0   
198           0            0  ...          0    0        0      0      0   
199           0            0  ...          0    0        0      0      0   

     youtube  yr  zero  zika  zumwalt  
0          0   0     0     0        0  
1          0   0     0     0        0  
2          0   0     0     0        4  
3          0   0     0     0        0  
4          0   0     0     0        0  
..       ...  ..   ...   ...      ...  
195        0   0     0     0        0  
196        0   0     0     0        0  
197        0   0     0     0        0  
198        0   0     0     0        0  
199        0   0     0     0        0  

[200 rows x 1815 columns]

In [60]:
text_bow.toarray()

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 4],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]])

In [61]:
#Now, include these vectors as a new column named bow_vector in your datasets 

data_train['bow_vector']=text_bow[0:len(data_train)].toarray().tolist()

In [62]:
data_train

favorite_count                                          full_text  \
0                0  b"RT @KUSINews: One of our longtime viewers wa...   
1              258  b"Today I'm urging the @CDCgov to immediately ...   
2                0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                3  b'Pleased to support @amergateways at their Ju...   
..             ...                                                ...   
95            1720  b'Tragedy in my #CA15. Hold these grieving fam...   
96               1  b'\xf0\x9f\x9a\x9b\xf0\x9f\x9b\xa3 Had a great...   
97              28  b'This morning, I had a good, constructive dis...   
98               5  b"Met w/local leaders at @FoLARtweets Noche de...   
99               1  b'There are 4 weeks left to submit your apps a...   

                    hashtags  retweet_count    year party_id  party_class  \
0                       KUSI             10  2017.0        R            1   
1                Coronavirus            111  2020.0        R            1   
2                       MO03              2  2014.0        R            1   
3       TeamUSA WorldJuniors              3  2017.0        R            1   
4     ImmigrantHeritageMonth              3  2019.0        D            0   
..                       ...            ...     ...      ...          ...   
95                      CA15            176  2019.0        D            0   
96  Burlington WorkingforWA2              2  2019.0        D            0   
97       Cambridge taxreform              8  2018.0        R            1   
98                   LARiver              2  2017.0        D            0   
99                     CAC16              1  2016.0        D            0   

                                           text_clean  \
0     rt  kusinews  one longtime viewer congressma...   
1     today  urge  cdcgov immediately launch  phon...   
2   tomorrow   mo senior graduate calvary lutheran...   
3   congrats  teamusa canton native  jgreenway win...   
4   pleased support  amergateways june fiesta  hon...   
..                                                ...   
95  tragedy  ca  hold grieve family heart  http  c...   
96  xfxfxaxbxfxfxbxa great time visit students  am...   
97  this morning  good  constructive discussion  w...   
98    met local leader  folartweets noche del rio ...   
99  there  week leave submit apps win big  sign  c...   

                                           bow_vector  
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
..                                                ...  
95  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
96  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
97  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
98  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
99  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  

[100 rows x 9 columns]

In [63]:
data_train=pd.concat([data_train,text_bow_df[0:len(data_train)]], axis=1)

In [64]:
data_train

favorite_count                                          full_text  \
0                0  b"RT @KUSINews: One of our longtime viewers wa...   
1              258  b"Today I'm urging the @CDCgov to immediately ...   
2                0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                3  b'Pleased to support @amergateways at their Ju...   
..             ...                                                ...   
95            1720  b'Tragedy in my #CA15. Hold these grieving fam...   
96               1  b'\xf0\x9f\x9a\x9b\xf0\x9f\x9b\xa3 Had a great...   
97              28  b'This morning, I had a good, constructive dis...   
98               5  b"Met w/local leaders at @FoLARtweets Noche de...   
99               1  b'There are 4 weeks left to submit your apps a...   

                    hashtags  retweet_count    year party_id  party_class  \
0                       KUSI             10  2017.0        R            1   
1                Coronavirus            111  2020.0        R            1   
2                       MO03              2  2014.0        R            1   
3       TeamUSA WorldJuniors              3  2017.0        R            1   
4     ImmigrantHeritageMonth              3  2019.0        D            0   
..                       ...            ...     ...      ...          ...   
95                      CA15            176  2019.0        D            0   
96  Burlington WorkingforWA2              2  2019.0        D            0   
97       Cambridge taxreform              8  2018.0        R            1   
98                   LARiver              2  2017.0        D            0   
99                     CAC16              1  2016.0        D            0   

                                           text_clean  \
0     rt  kusinews  one longtime viewer congressma...   
1     today  urge  cdcgov immediately launch  phon...   
2   tomorrow   mo senior graduate calvary lutheran...   
3   congrats  teamusa canton native  jgreenway win...   
4   pleased support  amergateways june fiesta  hon...   
..                                                ...   
95  tragedy  ca  hold grieve family heart  http  c...   
96  xfxfxaxbxfxfxbxa great time visit students  am...   
97  this morning  good  constructive discussion  w...   
98    met local leader  folartweets noche del rio ...   
99  there  week leave submit apps win big  sign  c...   

                                           bow_vector  abcnews  ...  \
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
4   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
..                                                ...      ...  ...   
95  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
96  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
97  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
98  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
99  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   

    yesterday  yet  yorkers  young  youth  youtube  yr  zero  zika  zumwalt  
0           0    0        0      0      0        0   0     0     0        0  
1           0    0        0      0      0        0   0     0     0        0  
2           0    0        0      0      0        0   0     0     0        4  
3           0    0        0      0      0        0   0     0     0        0  
4           0    0        0      0      0        0   0     0     0        0  
..        ...  ...      ...    ...    ...      ...  ..   ...   ...      ...  
95          0    0        0      0      0        0   0     0     0        0  
96          0    0        0      0      

In [65]:
#Now, include these vectors as a new column named bow_vector in your datasets 

data_test['bow_vector']=text_bow[len(data_train):len(data)].toarray().tolist()

In [66]:
text_bow_df[len(data_train):len(data)]

abcnews  able  abortion  abrams  absolutely  aca  access  accessibility  \
100        0     0         0       0           0    0       0              0   
101        0     0         0       0           0    0       0              0   
102        0     0         0       0           0    0       0              0   
103        0     0         0       0           0    0       0              0   
104        0     1         0       0           0    0       0              0   
..       ...   ...       ...     ...         ...  ...     ...            ...   
195        0     0         0       0           0    0       0              0   
196        0     0         0       0           0    0       0              0   
197        0     0         0       0           0    0       0              0   
198        0     0         0       0           0    0       0              0   
199        0     0         0       0           0    0       0              0   

     accomplish  accordingly  ...  yesterday  yet  yorkers  young  youth  \
100           0            0  ...          0    0        0      0      0   
101           0            0  ...          0    0        0      0      0   
102           0            0  ...          0    0        0      0      1   
103           0            0  ...          0    0        0      0      0   
104           0            0  ...          0    0        0      0      0   
..          ...          ...  ...        ...  ...      ...    ...    ...   
195           0            0  ...          0    0        0      0      0   
196           0            0  ...          0    0        0      0      0   
197           0            0  ...          0    0        0      0      0   
198           0            0  ...          0    0        0      0      0   
199           0            0  ...          0    0        0      0      0   

     youtube  yr  zero  zika  zumwalt  
100        0   0     0     0        0  
101        0   0     0     0        0  
102        0   0     0     0        0  
103        0   0     0     0        0  
104        0   0     0     0        0  
..       ...  ..   ...   ...      ...  
195        0   0     0     0        0  
196        0   0     0     0        0  
197        0   0     0     0        0  
198        0   0     0     0        0  
199        0   0     0     0        0  

[100 rows x 1815 columns]

In [67]:
pd.DataFrame(data=text_bow_df[len(data_train):len(data)]).set_index(np.arange(len(data_train)))

abcnews  able  abortion  abrams  absolutely  aca  access  accessibility  \
0         0     0         0       0           0    0       0              0   
1         0     0         0       0           0    0       0              0   
2         0     0         0       0           0    0       0              0   
3         0     0         0       0           0    0       0              0   
4         0     1         0       0           0    0       0              0   
..      ...   ...       ...     ...         ...  ...     ...            ...   
95        0     0         0       0           0    0       0              0   
96        0     0         0       0           0    0       0              0   
97        0     0         0       0           0    0       0              0   
98        0     0         0       0           0    0       0              0   
99        0     0         0       0           0    0       0              0   

    accomplish  accordingly  ...  yesterday  yet  yorkers  young  youth  \
0            0            0  ...          0    0        0      0      0   
1            0            0  ...          0    0        0      0      0   
2            0            0  ...          0    0        0      0      1   
3            0            0  ...          0    0        0      0      0   
4            0            0  ...          0    0        0      0      0   
..         ...          ...  ...        ...  ...      ...    ...    ...   
95           0            0  ...          0    0        0      0      0   
96           0            0  ...          0    0        0      0      0   
97           0            0  ...          0    0        0      0      0   
98           0            0  ...          0    0        0      0      0   
99           0            0  ...          0    0        0      0      0   

    youtube  yr  zero  zika  zumwalt  
0         0   0     0     0        0  
1         0   0     0     0        0  
2         0   0     0     0        0  
3         0   0     0     0        0  
4         0   0     0     0        0  
..      ...  ..   ...   ...      ...  
95        0   0     0     0        0  
96        0   0     0     0        0  
97        0   0     0     0        0  
98        0   0     0     0        0  
99        0   0     0     0        0  

[100 rows x 1815 columns]

In [68]:
# To allow indexing to help the concatenate
data_test=pd.concat([data_test,pd.DataFrame(data=text_bow_df[len(data_train):len(data)]).set_index(np.arange(len(data_train)))], axis=1)

In [69]:
data_test

Id  favorite_count                                          full_text  \
0     0              70  b'#TaxReform improved the playing field for Am...   
1     2              49  b"\xe2\x80\x9cI became convinced that our gene...   
2     3              14  b'During #NationalAdoptionMonth, we honor the ...   
3     4              13  b'Happy #AirborneDay to our @USArmy paratroope...   
4     5              73  b"Proud to join 200+ colleagues in SCOTUS amic...   
..  ...             ...                                                ...   
95  103               2  b"Joining the CO Delegation in support of Gov ...   
96  104               7  b'.@SwiftTransport merger w/ @DriveKnight is g...   
97  105               7  b'Had a great time @ the Sentara Heart Hospita...   
98  106               3  b"Thank you to @arnoldporter for inviting me t...   
99  107               8  b'ICYMI: Rep. Tulsi Gabbard joins congressiona...   

                         hashtags  retweet_count    year party  \
0                       TaxReform             13  2018.0     D   
1      MeToo ShatteringTheSilence             24  2017.0     D   
2           NationalAdoptionMonth              2  2019.0     D   
3   AirborneDay AirborneAllTheWay              7  2018.0     D   
4                            LGBT             13  2017.0     D   
..                            ...            ...     ...   ...   
95                     copolitics              2  2015.0     D   
96                             AZ              6  2017.0     D   
97                      OurHearts              3  2020.0     D   
98                       COVID_19              2  2020.0     D   
99                           STEM              6  2015.0     D   

                                           text_clean  \
0      taxreform improve playing field american wo...   
1     xexci become convinced generation silence ma...   
2   during  nationaladoptionmonth  honor adoptive ...   
3   happy  airborneday  usarmy paratrooper veteran...   
4     proud join  colleague scotus amicus brief ar...   
..                                                ...   
95    joining co delegation support gov hickenloop...   
96      swifttransport merger   driveknight great ...   
97  had great time  sentara heart hospitalxexs ann...   
98    thank  arnoldporter invite join policymakers...   
99  icymi  rep tulsi gabbard join congressional le...   

                                           bow_vector  abcnews  ...  \
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
4   [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
..                                                ...      ...  ...   
95  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
96  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
97  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
98  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
99  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   

    yesterday  yet  yorkers  young  youth  youtube  yr  zero  zika  zumwalt  
0           0    0        0      0      0        0   0     0     0        0  
1           0    0        0      0      0        0   0     0     0        0  
2           0    0        0      0      1        0   0     0     0        0  
3           0    0        0      0      0        0   0     0     0        0  
4           0    0        0      0      0        0   0     0     0        0  
..        ...  ...      ...    ...    ...      ...  ..   ...   ...      ...  
95          0    0        0      0      0        0   0     0     0        0  
96          0    0        0      0      0        0   0     0     0        0  
97          0    0        0      0 

Word2vec similarity ler icin iyi ama bag of words gibi bir vektor dondurmuyor ya da ben bulamadim.

In [70]:
# Now apply bag of words to hashtags

#We do not apply preprocessing to that column because there exists a certain form for hashtags

# Bag of words
# Following from [1]
vectorizer = CountVectorizer()

hash_bow = vectorizer.fit_transform(data['hashtags'])
hash_bow_df = pd.DataFrame(hash_bow.toarray(),columns=vectorizer.get_feature_names())

In [71]:
hash_bow_df

1000days  4jobs  911remembrance  actonclimate  ada28  airbornealltheway  \
0           0      0               0             0      0                  0   
1           0      0               0             0      0                  0   
2           0      0               0             0      0                  0   
3           0      0               0             0      0                  0   
4           0      0               0             0      0                  0   
..        ...    ...             ...           ...    ...                ...   
195         0      0               0             0      0                  0   
196         0      0               0             0      0                  0   
197         0      0               0             0      0                  0   
198         0      0               0             0      0                  0   
199         0      0               0             0      0                  0   

     airborneday  al03  alzheimers  american  ...  welfarestate  wematter  \
0              0     0           0         0  ...             0         0   
1              0     0           0         0  ...             0         0   
2              0     0           0         0  ...             0         0   
3              0     0           0         0  ...             0         0   
4              0     0           0         0  ...             0         0   
..           ...   ...         ...       ...  ...           ...       ...   
195            0     0           0         0  ...             0         0   
196            0     0           0         0  ...             0         0   
197            0     0           0         0  ...             0         0   
198            0     0           0         0  ...             0         0   
199            0     0           0         0  ...             0         0   

     whiteandgold  who  whywemarch  wnba  workingforwa2  worldjuniors  \
0               0    0           0     0              0             0   
1               0    0           0     0              0             0   
2               0    0           0     0              0             0   
3               0    0           0     0              0             1   
4               0    0           0     0              0             0   
..            ...  ...         ...   ...            ...           ...   
195             0    0           0     0              0             0   
196             0    0           0     0              0             0   
197             0    0           0     0              0             0   
198             0    0           0     0              0             0   
199             0    0           0     0              0             0   

     worldseries  zika  
0              0     0  
1              0     0  
2              0     0  
3              0     0  
4              0     0  
..           ...   ...  
195            0     0  
196            0     0  
197            0     0  
198            0     0  
199            0     0  

[200 rows x 252 columns]

In [72]:
data_train=pd.concat([data_train,hash_bow_df[0:len(data_train)]], axis=1)

In [73]:
data_train

favorite_count                                          full_text  \
0                0  b"RT @KUSINews: One of our longtime viewers wa...   
1              258  b"Today I'm urging the @CDCgov to immediately ...   
2                0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3                9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4                3  b'Pleased to support @amergateways at their Ju...   
..             ...                                                ...   
95            1720  b'Tragedy in my #CA15. Hold these grieving fam...   
96               1  b'\xf0\x9f\x9a\x9b\xf0\x9f\x9b\xa3 Had a great...   
97              28  b'This morning, I had a good, constructive dis...   
98               5  b"Met w/local leaders at @FoLARtweets Noche de...   
99               1  b'There are 4 weeks left to submit your apps a...   

                    hashtags  retweet_count    year party_id  party_class  \
0                       KUSI             10  2017.0        R            1   
1                Coronavirus            111  2020.0        R            1   
2                       MO03              2  2014.0        R            1   
3       TeamUSA WorldJuniors              3  2017.0        R            1   
4     ImmigrantHeritageMonth              3  2019.0        D            0   
..                       ...            ...     ...      ...          ...   
95                      CA15            176  2019.0        D            0   
96  Burlington WorkingforWA2              2  2019.0        D            0   
97       Cambridge taxreform              8  2018.0        R            1   
98                   LARiver              2  2017.0        D            0   
99                     CAC16              1  2016.0        D            0   

                                           text_clean  \
0     rt  kusinews  one longtime viewer congressma...   
1     today  urge  cdcgov immediately launch  phon...   
2   tomorrow   mo senior graduate calvary lutheran...   
3   congrats  teamusa canton native  jgreenway win...   
4   pleased support  amergateways june fiesta  hon...   
..                                                ...   
95  tragedy  ca  hold grieve family heart  http  c...   
96  xfxfxaxbxfxfxbxa great time visit students  am...   
97  this morning  good  constructive discussion  w...   
98    met local leader  folartweets noche del rio ...   
99  there  week leave submit apps win big  sign  c...   

                                           bow_vector  abcnews  ...  \
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
4   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
..                                                ...      ...  ...   
95  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
96  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
97  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
98  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
99  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   

    welfarestate  wematter  whiteandgold  who  whywemarch  wnba  \
0              0         0             0    0           0     0   
1              0         0             0    0           0     0   
2              0         0             0    0           0     0   
3              0         0             0    0           0     0   
4              0         0             0    0           0     0   
..           ...       ...           ...  ...         ...   ...   
95             0         0             0    0           0     0   
96             0         0             0    0           0     0   
97             0         0             0    0           0    

In [74]:
data_test

Id  favorite_count                                          full_text  \
0     0              70  b'#TaxReform improved the playing field for Am...   
1     2              49  b"\xe2\x80\x9cI became convinced that our gene...   
2     3              14  b'During #NationalAdoptionMonth, we honor the ...   
3     4              13  b'Happy #AirborneDay to our @USArmy paratroope...   
4     5              73  b"Proud to join 200+ colleagues in SCOTUS amic...   
..  ...             ...                                                ...   
95  103               2  b"Joining the CO Delegation in support of Gov ...   
96  104               7  b'.@SwiftTransport merger w/ @DriveKnight is g...   
97  105               7  b'Had a great time @ the Sentara Heart Hospita...   
98  106               3  b"Thank you to @arnoldporter for inviting me t...   
99  107               8  b'ICYMI: Rep. Tulsi Gabbard joins congressiona...   

                         hashtags  retweet_count    year party  \
0                       TaxReform             13  2018.0     D   
1      MeToo ShatteringTheSilence             24  2017.0     D   
2           NationalAdoptionMonth              2  2019.0     D   
3   AirborneDay AirborneAllTheWay              7  2018.0     D   
4                            LGBT             13  2017.0     D   
..                            ...            ...     ...   ...   
95                     copolitics              2  2015.0     D   
96                             AZ              6  2017.0     D   
97                      OurHearts              3  2020.0     D   
98                       COVID_19              2  2020.0     D   
99                           STEM              6  2015.0     D   

                                           text_clean  \
0      taxreform improve playing field american wo...   
1     xexci become convinced generation silence ma...   
2   during  nationaladoptionmonth  honor adoptive ...   
3   happy  airborneday  usarmy paratrooper veteran...   
4     proud join  colleague scotus amicus brief ar...   
..                                                ...   
95    joining co delegation support gov hickenloop...   
96      swifttransport merger   driveknight great ...   
97  had great time  sentara heart hospitalxexs ann...   
98    thank  arnoldporter invite join policymakers...   
99  icymi  rep tulsi gabbard join congressional le...   

                                           bow_vector  abcnews  ...  \
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
4   [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
..                                                ...      ...  ...   
95  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
96  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
97  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
98  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
99  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   

    yesterday  yet  yorkers  young  youth  youtube  yr  zero  zika  zumwalt  
0           0    0        0      0      0        0   0     0     0        0  
1           0    0        0      0      0        0   0     0     0        0  
2           0    0        0      0      1        0   0     0     0        0  
3           0    0        0      0      0        0   0     0     0        0  
4           0    0        0      0      0        0   0     0     0        0  
..        ...  ...      ...    ...    ...      ...  ..   ...   ...      ...  
95          0    0        0      0      0        0   0     0     0        0  
96          0    0        0      0      0        0   0     0     0        0  
97          0    0        0      0 

In [75]:
hash_bow_df[len(data_train):len(data)]

1000days  4jobs  911remembrance  actonclimate  ada28  airbornealltheway  \
100         0      0               0             0      0                  0   
101         0      0               0             0      0                  0   
102         0      0               0             0      0                  0   
103         0      0               0             0      0                  1   
104         0      0               0             0      0                  0   
..        ...    ...             ...           ...    ...                ...   
195         0      0               0             0      0                  0   
196         0      0               0             0      0                  0   
197         0      0               0             0      0                  0   
198         0      0               0             0      0                  0   
199         0      0               0             0      0                  0   

     airborneday  al03  alzheimers  american  ...  welfarestate  wematter  \
100            0     0           0         0  ...             0         0   
101            0     0           0         0  ...             0         0   
102            0     0           0         0  ...             0         0   
103            1     0           0         0  ...             0         0   
104            0     0           0         0  ...             0         0   
..           ...   ...         ...       ...  ...           ...       ...   
195            0     0           0         0  ...             0         0   
196            0     0           0         0  ...             0         0   
197            0     0           0         0  ...             0         0   
198            0     0           0         0  ...             0         0   
199            0     0           0         0  ...             0         0   

     whiteandgold  who  whywemarch  wnba  workingforwa2  worldjuniors  \
100             0    0           0     0              0             0   
101             0    0           0     0              0             0   
102             0    0           0     0              0             0   
103             0    0           0     0              0             0   
104             0    0           0     0              0             0   
..            ...  ...         ...   ...            ...           ...   
195             0    0           0     0              0             0   
196             0    0           0     0              0             0   
197             0    0           0     0              0             0   
198             0    0           0     0              0             0   
199             0    0           0     0              0             0   

     worldseries  zika  
100            0     0  
101            0     0  
102            0     0  
103            0     0  
104            0     0  
..           ...   ...  
195            0     0  
196            0     0  
197            0     0  
198            0     0  
199            0     0  

[100 rows x 252 columns]

In [76]:
#data_test=pd.concat([data_test,hash_bow_df[len(data_train):len(data)]], axis=1)
# To allow indexing to help the concatenate
data_test=pd.concat([data_test,pd.DataFrame(data=hash_bow_df[len(data_train):len(data)]).set_index(np.arange(len(data_train)))], axis=1)

In [77]:
data_test

Id  favorite_count                                          full_text  \
0     0              70  b'#TaxReform improved the playing field for Am...   
1     2              49  b"\xe2\x80\x9cI became convinced that our gene...   
2     3              14  b'During #NationalAdoptionMonth, we honor the ...   
3     4              13  b'Happy #AirborneDay to our @USArmy paratroope...   
4     5              73  b"Proud to join 200+ colleagues in SCOTUS amic...   
..  ...             ...                                                ...   
95  103               2  b"Joining the CO Delegation in support of Gov ...   
96  104               7  b'.@SwiftTransport merger w/ @DriveKnight is g...   
97  105               7  b'Had a great time @ the Sentara Heart Hospita...   
98  106               3  b"Thank you to @arnoldporter for inviting me t...   
99  107               8  b'ICYMI: Rep. Tulsi Gabbard joins congressiona...   

                         hashtags  retweet_count    year party  \
0                       TaxReform             13  2018.0     D   
1      MeToo ShatteringTheSilence             24  2017.0     D   
2           NationalAdoptionMonth              2  2019.0     D   
3   AirborneDay AirborneAllTheWay              7  2018.0     D   
4                            LGBT             13  2017.0     D   
..                            ...            ...     ...   ...   
95                     copolitics              2  2015.0     D   
96                             AZ              6  2017.0     D   
97                      OurHearts              3  2020.0     D   
98                       COVID_19              2  2020.0     D   
99                           STEM              6  2015.0     D   

                                           text_clean  \
0      taxreform improve playing field american wo...   
1     xexci become convinced generation silence ma...   
2   during  nationaladoptionmonth  honor adoptive ...   
3   happy  airborneday  usarmy paratrooper veteran...   
4     proud join  colleague scotus amicus brief ar...   
..                                                ...   
95    joining co delegation support gov hickenloop...   
96      swifttransport merger   driveknight great ...   
97  had great time  sentara heart hospitalxexs ann...   
98    thank  arnoldporter invite join policymakers...   
99  icymi  rep tulsi gabbard join congressional le...   

                                           bow_vector  abcnews  ...  \
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
1   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
2   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
3   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
4   [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
..                                                ...      ...  ...   
95  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
96  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
97  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
98  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   
99  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...   

    welfarestate  wematter  whiteandgold  who  whywemarch  wnba  \
0              0         0             0    0           0     0   
1              0         0             0    0           0     0   
2              0         0             0    0           0     0   
3              0         0             0    0           0     0   
4              0         0             0    0           0     0   
..           ...       ...           ...  ...         ...   ...   
95             0         0             0    0           0     0   
96             0         0             0    0           0     0   
97             0         0             0    0           0     0   
98             0         0             0    0           0     0   


In [78]:
# Now Word2vec

# Following from [2]

model = gensim.models.Word2Vec(data['text_clean'], min_count = 1)

In [79]:
model

## Apply dimensionality reduction to bow_vector and decrease it to 3 principal components

In [80]:
# Apply dimensionality reduction to both test and train sets simultaneously
text_bow_df

abcnews  able  abortion  abrams  absolutely  aca  access  accessibility  \
0          0     0         0       0           0    0       0              0   
1          0     0         0       0           0    0       0              0   
2          0     0         0       0           0    0       0              0   
3          0     0         0       0           0    0       0              0   
4          0     0         0       0           0    0       0              0   
..       ...   ...       ...     ...         ...  ...     ...            ...   
195        0     0         0       0           0    0       0              0   
196        0     0         0       0           0    0       0              0   
197        0     0         0       0           0    0       0              0   
198        0     0         0       0           0    0       0              0   
199        0     0         0       0           0    0       0              0   

     accomplish  accordingly  ...  yesterday  yet  yorkers  young  youth  \
0             0            0  ...          0    0        0      0      0   
1             0            0  ...          0    0        0      0      0   
2             0            0  ...          0    0        0      0      0   
3             0            0  ...          0    0        0      0      0   
4             0            0  ...          0    0        0      0      0   
..          ...          ...  ...        ...  ...      ...    ...    ...   
195           0            0  ...          0    0        0      0      0   
196           0            0  ...          0    0        0      0      0   
197           0            0  ...          0    0        0      0      0   
198           0            0  ...          0    0        0      0      0   
199           0            0  ...          0    0        0      0      0   

     youtube  yr  zero  zika  zumwalt  
0          0   0     0     0        0  
1          0   0     0     0        0  
2          0   0     0     0        4  
3          0   0     0     0        0  
4          0   0     0     0        0  
..       ...  ..   ...   ...      ...  
195        0   0     0     0        0  
196        0   0     0     0        0  
197        0   0     0     0        0  
198        0   0     0     0        0  
199        0   0     0     0        0  

[200 rows x 1815 columns]

In [81]:
# from HW6
#Following from [5] to use sklearn's PCA 

#Standardize before calling PCA
scaler=preprocessing.StandardScaler().fit(text_bow_df)
text_bow_df_scaled=scaler.transform(text_bow_df) 

sklearn_pca = PCA(n_components=3)
pcs = sklearn_pca.fit_transform(text_bow_df_scaled)

In [82]:
pcs

array([[ 3.58004272e-02,  4.76499313e-01, -4.54763883e-01],
       [-2.93180796e-02, -3.01236648e+00,  2.71050667e+00],
       [-4.15603526e-01,  2.20952252e-01, -7.58794962e-01],
       [-6.16861021e-01,  1.95661684e-01, -8.46422417e-01],
       [-3.19292913e+00,  3.65864015e+00,  6.05753640e-01],
       [ 2.21907945e-01, -4.55321645e+00, -3.35092016e+00],
       [ 5.15101256e-01, -5.04815712e-01,  1.59780382e+00],
       [-4.36799825e-01,  3.52255411e-01, -4.53131572e-01],
       [-3.99604127e-01, -2.59267443e-01, -7.91926345e-01],
       [-3.63348296e-01, -6.37378888e-03, -3.33109149e-01],
       [-7.63890550e-01,  1.88516549e+00, -2.18377352e+00],
       [-3.62586079e-01, -8.52026883e-02, -5.14763297e-01],
       [-6.20706430e-01, -3.94926502e-01,  4.90374412e-01],
       [-3.95992324e-01, -4.41082510e-01, -8.91022062e-01],
       [-1.41724356e+00,  1.22562685e+00, -1.33837584e+00],
       [-6.71747446e-01, -5.14894697e-01,  4.38254570e-01],
       [ 3.46259225e-01, -3.65884714e-02

In [83]:
# Add pcs to the original data
data_train['bow_pcs']=pcs[0:len(data_train)].tolist()

In [84]:
data_train.head()

favorite_count                                          full_text  \
0               0  b"RT @KUSINews: One of our longtime viewers wa...   
1             258  b"Today I'm urging the @CDCgov to immediately ...   
2               0  b'Tomorrow, #MO03 seniors graduate from Calvar...   
3               9  b'Congrats to #TeamUSA and Canton Native @JGre...   
4               3  b'Pleased to support @amergateways at their Ju...   

                 hashtags  retweet_count    year party_id  party_class  \
0                    KUSI             10  2017.0        R            1   
1             Coronavirus            111  2020.0        R            1   
2                    MO03              2  2014.0        R            1   
3    TeamUSA WorldJuniors              3  2017.0        R            1   
4  ImmigrantHeritageMonth              3  2019.0        D            0   

                                          text_clean  \
0    rt  kusinews  one longtime viewer congressma...   
1    today  urge  cdcgov immediately launch  phon...   
2  tomorrow   mo senior graduate calvary lutheran...   
3  congrats  teamusa canton native  jgreenway win...   
4  pleased support  amergateways june fiesta  hon...   

                                          bow_vector  abcnews  ...  wematter  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
2  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   

   whiteandgold  who  whywemarch  wnba  workingforwa2  worldjuniors  \
0             0    0           0     0              0             0   
1             0    0           0     0              0             0   
2             0    0           0     0              0             0   
3             0    0           0     0              0             1   
4             0    0           0     0              0             0   

   worldseries  zika                                            bow_pcs  
0            0     0  [0.03580042722827309, 0.47649931268928214, -0....  
1            0     0  [-0.029318079614505006, -3.012366478145435, 2....  
2            0     0  [-0.41560352603614215, 0.22095225160228846, -0...  
3            0     0  [-0.6168610209407865, 0.19566168363213765, -0....  
4            0     0  [-3.192929125377964, 3.65864015054891, 0.60575...  

[5 rows x 2077 columns]

In [85]:
len(pcs[len(data_train):len(data)].tolist())

100

In [86]:
data_test['bow_pcs']=pcs[len(data_train):len(data)].tolist()

In [87]:
data_test.head()

Id  favorite_count                                          full_text  \
0   0              70  b'#TaxReform improved the playing field for Am...   
1   2              49  b"\xe2\x80\x9cI became convinced that our gene...   
2   3              14  b'During #NationalAdoptionMonth, we honor the ...   
3   4              13  b'Happy #AirborneDay to our @USArmy paratroope...   
4   5              73  b"Proud to join 200+ colleagues in SCOTUS amic...   

                        hashtags  retweet_count    year party  \
0                      TaxReform             13  2018.0     D   
1     MeToo ShatteringTheSilence             24  2017.0     D   
2          NationalAdoptionMonth              2  2019.0     D   
3  AirborneDay AirborneAllTheWay              7  2018.0     D   
4                           LGBT             13  2017.0     D   

                                          text_clean  \
0     taxreform improve playing field american wo...   
1    xexci become convinced generation silence ma...   
2  during  nationaladoptionmonth  honor adoptive ...   
3  happy  airborneday  usarmy paratrooper veteran...   
4    proud join  colleague scotus amicus brief ar...   

                                          bow_vector  abcnews  ...  wematter  \
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
2  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   
4  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...        0  ...         0   

   whiteandgold  who  whywemarch  wnba  workingforwa2  worldjuniors  \
0             0    0           0     0              0             0   
1             0    0           0     0              0             0   
2             0    0           0     0              0             0   
3             0    0           0     0              0             0   
4             0    0           0     0              0             0   

   worldseries  zika                                            bow_pcs  
0            0     0  [-0.5674686282631018, -0.34992609192330043, 0....  
1            0     0  [-0.774051856241835, -2.6125917747656833, 1.35...  
2            0     0  [3.3587136060754137, -2.3486411558352067, 1.07...  
3            0     0  [-0.5233835204434641, -0.07040349738815206, -0...  
4            0     0  [-0.4048106642908183, -0.4688231466696975, 0.2...  

[5 rows x 2077 columns]

In [88]:
#Plot like in HW6 with only the first 2 components

In [89]:
data_train['bow_pcs'][0][0]

0.03580042722827309

In [90]:
bow_pc1=np.zeros(len(data_train))
bow_pc2=np.zeros(len(data_train))
bow_pc3=np.zeros(len(data_train))

In [91]:
for i in np.arange(len(data_train)):
    bow_pc1[i]=data_train['bow_pcs'][i][0]
    bow_pc2[i]=data_train['bow_pcs'][i][1]
    bow_pc3[i]=data_train['bow_pcs'][i][2]

In [92]:
data_train['bow_pc1']=bow_pc1
data_train['bow_pc2']=bow_pc2
data_train['bow_pc3']=bow_pc3

In [93]:
#Add these columns to the test data

bow_pc1=np.zeros(len(data_test))
bow_pc2=np.zeros(len(data_test))
bow_pc3=np.zeros(len(data_test))

In [94]:
for i in np.arange(len(data_test)):
    bow_pc1[i]=data_test['bow_pcs'][i][0]
    bow_pc2[i]=data_test['bow_pcs'][i][1]
    bow_pc3[i]=data_test['bow_pcs'][i][2]

In [95]:
data_test['bow_pc1']=bow_pc1
data_test['bow_pc2']=bow_pc2
data_test['bow_pc3']=bow_pc3

In [96]:
# visualization_code.py
# Directly copy-pasted from the provided file

mpl.rcParams['figure.dpi'] = 600
plt.rcParams['figure.figsize'] = (20.0, 10.0)
plt.rcParams['font.family'] = "serif"
plt.rcParams['font.size'] = 10

df = data_train
pal = sns.color_palette("Paired")[:len(set(data_train['party_class']))]
p1 = sns.scatterplot(x="bow_pc1", y='bow_pc2', hue='party_class', palette = pal, data=df, s=250, alpha=0.7, legend=False)

#For each point, we add a text inside the bubble
for line in range(0,df.shape[0]):
     p1.text(df.bow_pc1[line], df.bow_pc2[line], df.party_class[line], horizontalalignment='left', size='medium', color='black', weight='semibold')

plt.suptitle('Two-Dimensional Map (PCA)', fontsize=36)
plt.xlabel('Dimension 1', fontsize=24)
plt.ylabel('Dimension 2', fontsize=24)


for i in df.party_class.unique():
    # get the convex hull
    points = df[df.party_class == i][['bow_pc1', 'bow_pc2']].values
    hull = ConvexHull(points)
    x_hull = np.append(points[hull.vertices,0],
                       points[hull.vertices,0][0])
    y_hull = np.append(points[hull.vertices,1],
                       points[hull.vertices,1][0])
    
    # interpolate
    dist = np.sqrt((x_hull[:-1] - x_hull[1:])**2 + (y_hull[:-1] - y_hull[1:])**2)
    dist_along = np.concatenate(([0], dist.cumsum()))
    spline, u = interpolate.splprep([x_hull, y_hull], 
                                    u=dist_along, s=0)
    interp_d = np.linspace(dist_along[0], dist_along[-1], 50)
    interp_x, interp_y = interpolate.splev(interp_d, spline)
    # plot shape
    plt.fill(interp_x, interp_y, '--', c=pal[i], alpha=0.2)
    

plt.grid()
plt.show()

In [97]:
# bow_vector dimensionality reduction with HW6 spectral embedding
#Following from HW6

In [98]:
#Following from sklearn's guides [4]

embedding = SpectralEmbedding(n_components=3)
pcs_embedded = embedding.fit_transform(text_bow_df_scaled) #Use the scaled version of bow_vec column for all of the data

In [99]:
data_train['bow_spec']=pcs_embedded[0:len(data_train)].tolist()

In [100]:
data_test['bow_spec']=pcs_embedded[len(data_train):len(data)].tolist()

In [101]:
bow_pc1=np.zeros(len(data_train))
bow_pc2=np.zeros(len(data_train))
bow_pc3=np.zeros(len(data_train))

In [102]:
for i in np.arange(len(data_train)):
    bow_pc1[i]=data_train['bow_spec'][i][0]
    bow_pc2[i]=data_train['bow_spec'][i][1]
    bow_pc3[i]=data_train['bow_spec'][i][2]

In [103]:
data_train['bow_spec1']=bow_pc1
data_train['bow_spec2']=bow_pc2
data_train['bow_spec3']=bow_pc3

In [104]:
#Add these columns to the test data

bow_pc1=np.zeros(len(data_test))
bow_pc2=np.zeros(len(data_test))
bow_pc3=np.zeros(len(data_test))

In [105]:
for i in np.arange(len(data_test)):
    bow_pc1[i]=data_test['bow_spec'][i][0]
    bow_pc2[i]=data_test['bow_spec'][i][1]
    bow_pc3[i]=data_test['bow_spec'][i][2]

In [106]:
data_test['bow_spec1']=bow_pc1
data_test['bow_spec2']=bow_pc2
data_test['bow_spec3']=bow_pc3

In [107]:
# visualization_code.py
# Directly copy-pasted from the provided file

mpl.rcParams['figure.dpi'] = 600
plt.rcParams['figure.figsize'] = (20.0, 10.0)
plt.rcParams['font.family'] = "serif"
plt.rcParams['font.size'] = 10

df = data_train
pal = sns.color_palette("Paired")[:len(set(data_train['party_class']))]
p1 = sns.scatterplot(x="bow_spec1", y='bow_spec2', hue='party_class', palette = pal, data=df, s=250, alpha=0.7, legend=False)

#For each point, we add a text inside the bubble
for line in range(0,df.shape[0]):
     p1.text(df.bow_spec1[line], df.bow_spec2[line], df.party_class[line], horizontalalignment='left', size='medium', color='black', weight='semibold')

plt.suptitle('Two-Dimensional Map (Spectral Embedding)', fontsize=36)
plt.xlabel('Dimension 1', fontsize=24)
plt.ylabel('Dimension 2', fontsize=24)


for i in df.party_class.unique():
    # get the convex hull
    points = df[df.party_class == i][['bow_spec1', 'bow_spec2']].values
    hull = ConvexHull(points)
    x_hull = np.append(points[hull.vertices,0],
                       points[hull.vertices,0][0])
    y_hull = np.append(points[hull.vertices,1],
                       points[hull.vertices,1][0])
    
    # interpolate
    dist = np.sqrt((x_hull[:-1] - x_hull[1:])**2 + (y_hull[:-1] - y_hull[1:])**2)
    dist_along = np.concatenate(([0], dist.cumsum()))
    spline, u = interpolate.splprep([x_hull, y_hull], 
                                    u=dist_along, s=0)
    interp_d = np.linspace(dist_along[0], dist_along[-1], 50)
    interp_x, interp_y = interpolate.splev(interp_d, spline)
    # plot shape
    plt.fill(interp_x, interp_y, '--', c=pal[i], alpha=0.2)
    

plt.grid()
plt.show()

In [108]:
# bow_vector dimensionality reduction with HW6 t-SNE
#Following from HW6

In [109]:
pcs_tsne = TSNE(n_components=3).fit_transform(text_bow_df_scaled)

In [110]:
data_train['bow_tsne']=pcs_tsne[0:len(data_train)].tolist()

In [111]:
data_test['bow_tsne']=pcs_tsne[len(data_train):len(data)].tolist()

In [112]:
bow_pc1=np.zeros(len(data_train))
bow_pc2=np.zeros(len(data_train))
bow_pc3=np.zeros(len(data_train))

In [113]:
for i in np.arange(len(data_train)):
    bow_pc1[i]=data_train['bow_tsne'][i][0]
    bow_pc2[i]=data_train['bow_tsne'][i][1]
    bow_pc3[i]=data_train['bow_tsne'][i][2]

In [114]:
data_train['bow_tsne1']=bow_pc1
data_train['bow_tsne2']=bow_pc2
data_train['bow_tsne3']=bow_pc3

In [115]:
#Add these columns to the test data

bow_pc1=np.zeros(len(data_test))
bow_pc2=np.zeros(len(data_test))
bow_pc3=np.zeros(len(data_test))

In [116]:
for i in np.arange(len(data_test)):
    bow_pc1[i]=data_test['bow_tsne'][i][0]
    bow_pc2[i]=data_test['bow_tsne'][i][1]
    bow_pc3[i]=data_test['bow_tsne'][i][2]

In [117]:
data_test['bow_tsne1']=bow_pc1
data_test['bow_tsne2']=bow_pc2
data_test['bow_tsne3']=bow_pc3

In [118]:
# visualization_code.py
# Directly copy-pasted from the provided file

mpl.rcParams['figure.dpi'] = 600
plt.rcParams['figure.figsize'] = (20.0, 10.0)
plt.rcParams['font.family'] = "serif"
plt.rcParams['font.size'] = 10

df = data_train
pal = sns.color_palette("Paired")[:len(set(data_train['party_class']))]
p1 = sns.scatterplot(x="bow_tsne1", y='bow_tsne2', hue='party_class', palette = pal, data=df, s=250, alpha=0.7, legend=False)

#For each point, we add a text inside the bubble
for line in range(0,df.shape[0]):
     p1.text(df.bow_tsne1[line], df.bow_tsne2[line], df.party_class[line], horizontalalignment='left', size='medium', color='black', weight='semibold')

plt.suptitle('Two-Dimensional Map (t-SNE)', fontsize=36)
plt.xlabel('Dimension 1', fontsize=24)
plt.ylabel('Dimension 2', fontsize=24)


for i in df.party_class.unique():
    # get the convex hull
    points = df[df.party_class == i][['bow_tsne1', 'bow_tsne2']].values
    hull = ConvexHull(points)
    x_hull = np.append(points[hull.vertices,0],
                       points[hull.vertices,0][0])
    y_hull = np.append(points[hull.vertices,1],
                       points[hull.vertices,1][0])
    
    # interpolate
    dist = np.sqrt((x_hull[:-1] - x_hull[1:])**2 + (y_hull[:-1] - y_hull[1:])**2)
    dist_along = np.concatenate(([0], dist.cumsum()))
    spline, u = interpolate.splprep([x_hull, y_hull], 
                                    u=dist_along, s=0)
    interp_d = np.linspace(dist_along[0], dist_along[-1], 50)
    interp_x, interp_y = interpolate.splev(interp_d, spline)
    # plot shape
    plt.fill(interp_x, interp_y, '--', c=pal[i], alpha=0.2)
    

plt.grid()
plt.show()

## Create X_train, y_train

In [119]:
X_train=data_train.loc[:, data_train.columns != 'party_id']

In [120]:
X_train=X_train.loc[:, X_train.columns != 'full_text']

In [121]:
X_train=X_train.loc[:, X_train.columns != 'party_class']

In [122]:
X_train=X_train.loc[:, X_train.columns != 'text_clean']

In [123]:
X_train=X_train.loc[:, X_train.columns != 'hashtags']

In [124]:
X_train=X_train.loc[:, X_train.columns != 'bow_vector']

In [125]:
X_train=X_train.loc[:, X_train.columns != 'bow_spec']

In [126]:
X_train=X_train.loc[:, X_train.columns != 'bow_tsne']

In [127]:
X_train=X_train.loc[:, X_train.columns != 'bow_pcs']

In [128]:
X_train

favorite_count  retweet_count    year  abcnews  able  abortion  abrams  \
0                0             10  2017.0        0     0         0       0   
1              258            111  2020.0        0     0         0       0   
2                0              2  2014.0        0     0         0       0   
3                9              3  2017.0        0     0         0       0   
4                3              3  2019.0        0     0         0       0   
..             ...            ...     ...      ...   ...       ...     ...   
95            1720            176  2019.0        0     0         0       0   
96               1              2  2019.0        0     0         0       0   
97              28              8  2018.0        0     0         0       0   
98               5              2  2017.0        0     0         0       0   
99               1              1  2016.0        0     0         0       0   

    absolutely  aca  access  ...  zika   bow_pc1    bow_pc2    bow_pc3  \
0            0    0       0  ...     0  0.035800   0.476499  -0.454764   
1            0    0       0  ...     0 -0.029318  -3.012366   2.710507   
2            0    0       0  ...     0 -0.415604   0.220952  -0.758795   
3            0    0       0  ...     0 -0.616861   0.195662  -0.846422   
4            0    0       0  ...     0 -3.192929   3.658640   0.605754   
..         ...  ...     ...  ...   ...       ...        ...        ...   
95           0    0       0  ...     0 -0.363031   0.195922  -0.316556   
96           0    0       0  ...     0 -0.720607  -1.372497  -2.908082   
97           0    0       0  ...     0 -0.304784   2.598945  -1.198380   
98           0    0       0  ...     0 -1.652893 -13.862187  54.323792   
99           0    0       0  ...     0 -0.558381  -0.275912  -0.064386   

    bow_spec1  bow_spec2  bow_spec3   bow_tsne1   bow_tsne2   bow_tsne3  
0    0.010146  -0.003825  -0.001798 -112.039619 -108.548744   -7.316100  
1   -0.007385   0.038849  -0.025337  -99.995544  -37.590397 -116.876801  
2    0.010146  -0.003825  -0.001798   28.277555  -72.371971  210.781052  
3   -0.015808  -0.010316  -0.004607   47.616013  134.119476   22.153780  
4   -0.015808  -0.010316  -0.004607  -51.282043  152.328903   66.466370  
..        ...        ...        ...         ...         ...         ...  
95   0.000022   0.000108   0.000005    2.738613  -96.402504   -8.666757  
96  -0.015808  -0.010316  -0.004607  159.550186    4.630407   61.589588  
97  -0.007385   0.038849  -0.025337    7.850263   40.945190 -117.737854  
98   0.003989  -0.013730  -0.000523  -61.353710 -118.110573  -58.619637  
99  -0.015808  -0.010316  -0.004607  -79.225845  -86.646431   64.854485  

[100 rows x 2079 columns]

In [129]:
y_train=data_train['party_class']

In [130]:
y_train= pd.DataFrame(y_train)

In [131]:
y_train

party_class
0             1
1             1
2             1
3             1
4             0
..          ...
95            0
96            0
97            1
98            0
99            0

[100 rows x 1 columns]

In [132]:
# Two columns with the same name
X_train['year']

year  year
0   2017.0     0
1   2020.0     0
2   2014.0     0
3   2017.0     0
4   2019.0     0
..     ...   ...
95  2019.0     0
96  2019.0     0
97  2018.0     0
98  2017.0     0
99  2016.0     0

[100 rows x 2 columns]

In [133]:
X_train['Year']=X_train.iloc[:,2]

In [134]:
X_train.columns

Index(['favorite_count', 'retweet_count', 'year', 'abcnews', 'able',
       'abortion', 'abrams', 'absolutely', 'aca', 'access',
       ...
       'bow_pc1', 'bow_pc2', 'bow_pc3', 'bow_spec1', 'bow_spec2', 'bow_spec3',
       'bow_tsne1', 'bow_tsne2', 'bow_tsne3', 'Year'],
      dtype='object', length=2080)

In [135]:
X_train['Year']

0     2017.0
1     2020.0
2     2014.0
3     2017.0
4     2019.0
       ...  
95    2019.0
96    2019.0
97    2018.0
98    2017.0
99    2016.0
Name: Year, Length: 100, dtype: float64

Remove columns named year now,that means removing the year column coming from the bag of words method but that is fine as this would already not be adding information about the political view. 

In [136]:
#Remove the columns named 'year'

del X_train["year"]

In [137]:
X_train

favorite_count  retweet_count  abcnews  able  abortion  abrams  \
0                0             10        0     0         0       0   
1              258            111        0     0         0       0   
2                0              2        0     0         0       0   
3                9              3        0     0         0       0   
4                3              3        0     0         0       0   
..             ...            ...      ...   ...       ...     ...   
95            1720            176        0     0         0       0   
96               1              2        0     0         0       0   
97              28              8        0     0         0       0   
98               5              2        0     0         0       0   
99               1              1        0     0         0       0   

    absolutely  aca  access  accessibility  ...   bow_pc1    bow_pc2  \
0            0    0       0              0  ...  0.035800   0.476499   
1            0    0       0              0  ... -0.029318  -3.012366   
2            0    0       0              0  ... -0.415604   0.220952   
3            0    0       0              0  ... -0.616861   0.195662   
4            0    0       0              0  ... -3.192929   3.658640   
..         ...  ...     ...            ...  ...       ...        ...   
95           0    0       0              0  ... -0.363031   0.195922   
96           0    0       0              0  ... -0.720607  -1.372497   
97           0    0       0              0  ... -0.304784   2.598945   
98           0    0       0              0  ... -1.652893 -13.862187   
99           0    0       0              0  ... -0.558381  -0.275912   

      bow_pc3  bow_spec1  bow_spec2  bow_spec3   bow_tsne1   bow_tsne2  \
0   -0.454764   0.010146  -0.003825  -0.001798 -112.039619 -108.548744   
1    2.710507  -0.007385   0.038849  -0.025337  -99.995544  -37.590397   
2   -0.758795   0.010146  -0.003825  -0.001798   28.277555  -72.371971   
3   -0.846422  -0.015808  -0.010316  -0.004607   47.616013  134.119476   
4    0.605754  -0.015808  -0.010316  -0.004607  -51.282043  152.328903   
..        ...        ...        ...        ...         ...         ...   
95  -0.316556   0.000022   0.000108   0.000005    2.738613  -96.402504   
96  -2.908082  -0.015808  -0.010316  -0.004607  159.550186    4.630407   
97  -1.198380  -0.007385   0.038849  -0.025337    7.850263   40.945190   
98  54.323792   0.003989  -0.013730  -0.000523  -61.353710 -118.110573   
99  -0.064386  -0.015808  -0.010316  -0.004607  -79.225845  -86.646431   

     bow_tsne3    Year  
0    -7.316100  2017.0  
1  -116.876801  2020.0  
2   210.781052  2014.0  
3    22.153780  2017.0  
4    66.466370  2019.0  
..         ...     ...  
95   -8.666757  2019.0  
96   61.589588  2019.0  
97 -117.737854  2018.0  
98  -58.619637  2017.0  
99   64.854485  2016.0  

[100 rows x 2078 columns]

In [138]:
# Apply the same to X_test

In [139]:
X_test=data_test.loc[:, data_test.columns != 'party_id']

In [140]:
X_test=X_test.loc[:, X_test.columns != 'party']

In [141]:
X_test=X_test.loc[:, X_test.columns != 'full_text']

In [142]:
X_test=X_test.loc[:, X_test.columns != 'party_class']

In [143]:
X_test=X_test.loc[:, X_test.columns != 'text_clean']

In [144]:
X_test=X_test.loc[:, X_test.columns != 'hashtags']

In [145]:
X_test=X_test.loc[:, X_test.columns != 'bow_vector']

In [146]:
X_test=X_test.loc[:, X_test.columns != 'bow_spec']

In [147]:
X_test=X_test.loc[:, X_test.columns != 'bow_tsne']

In [148]:
X_test=X_test.loc[:, X_test.columns != 'bow_pcs']

In [149]:
X_test #Id column is not considered as a column!

Id  favorite_count  retweet_count    year  abcnews  able  abortion  \
0     0              70             13  2018.0        0     0         0   
1     2              49             24  2017.0        0     0         0   
2     3              14              2  2019.0        0     0         0   
3     4              13              7  2018.0        0     0         0   
4     5              73             13  2017.0        0     1         0   
..  ...             ...            ...     ...      ...   ...       ...   
95  103               2              2  2015.0        0     0         0   
96  104               7              6  2017.0        0     0         0   
97  105               7              3  2020.0        0     0         0   
98  106               3              2  2020.0        0     0         0   
99  107               8              6  2015.0        0     0         0   

    abrams  absolutely  aca  ...  zika   bow_pc1   bow_pc2   bow_pc3  \
0        0           0    0  ...     0 -0.567469 -0.349926  0.293677   
1        0           0    0  ...     0 -0.774052 -2.612592  1.351671   
2        0           0    0  ...     0  3.358714 -2.348641  1.073104   
3        0           0    0  ...     0 -0.523384 -0.070403 -0.284438   
4        0           0    0  ...     0 -0.404811 -0.468823  0.241219   
..     ...         ...  ...  ...   ...       ...       ...       ...   
95       0           0    0  ...     0 -0.605950  0.300588 -0.941803   
96       0           0    0  ...     0 -0.448118 -0.246125 -0.603387   
97       0           0    0  ...     0 -1.020344 -0.889460  0.399559   
98       0           0    0  ...     0 -0.475077  0.067007  0.608445   
99       0           0    0  ...     0 -0.667044  0.391776  1.726533   

    bow_spec1  bow_spec2  bow_spec3   bow_tsne1   bow_tsne2   bow_tsne3  
0   -0.000941  -0.004017  -0.002304  -39.652115   85.765099 -126.146332  
1   -0.015808  -0.010316  -0.004607  148.315414   10.649091  144.128922  
2   -0.015808  -0.010316  -0.004607   97.023636   20.537146   23.465921  
3   -0.015808  -0.010316  -0.004607 -209.083374  -36.940804  -79.505577  
4    0.012030  -0.003255   0.002279   14.436244  -68.395996  -54.968159  
..        ...        ...        ...         ...         ...         ...  
95  -0.015808  -0.010316  -0.004607 -131.731613   69.025620  146.894989  
96  -0.015808  -0.010316  -0.004607  -77.288391   22.221201   30.459713  
97   0.010146  -0.003825  -0.001798   -2.845464 -132.130524  -81.159874  
98   0.010146  -0.003825  -0.001798   20.978672   -0.568674  117.139458  
99  -0.007868   0.015335   0.042601   14.107494 -123.391586   99.250771  

[100 rows x 2080 columns]

In [150]:
# Two columns with the same name
X_test['year']

year  year
0   2018.0     0
1   2017.0     0
2   2019.0     0
3   2018.0     0
4   2017.0     0
..     ...   ...
95  2015.0     0
96  2017.0     0
97  2020.0     0
98  2020.0     0
99  2015.0     0

[100 rows x 2 columns]

In [151]:
X_test.iloc[:, 3]

0     2018.0
1     2017.0
2     2019.0
3     2018.0
4     2017.0
       ...  
95    2015.0
96    2017.0
97    2020.0
98    2020.0
99    2015.0
Name: year, Length: 100, dtype: float64

In [152]:
X_test['Year']=X_train.iloc[:,3]

In [153]:
#Remove the columns named 'year'

del X_test["year"]

Cannot feed a model with columns as a vector but if we add them all then it could be overfitting
But we do not need to worry because ElasticNet would take care of it

In [154]:
#Before we begin, check
np.where(np.isfinite(X_train)==False)

(array([], dtype=int64), array([], dtype=int64))

In [155]:
#Before we begin, check
np.where(np.isfinite(X_test)==False)

(array([], dtype=int64), array([], dtype=int64))

## Logistic regression with ElasticNet

In [156]:
# Following from [5] without cross validation because it takes so much time
elastic_net_classifier = LogisticRegressionCV(cv=None, penalty='elasticnet', solver='saga', l1_ratios=0.1*np.ones(np.shape(X_train)[1]))

In [157]:
X_train

favorite_count  retweet_count  abcnews  able  abortion  abrams  \
0                0             10        0     0         0       0   
1              258            111        0     0         0       0   
2                0              2        0     0         0       0   
3                9              3        0     0         0       0   
4                3              3        0     0         0       0   
..             ...            ...      ...   ...       ...     ...   
95            1720            176        0     0         0       0   
96               1              2        0     0         0       0   
97              28              8        0     0         0       0   
98               5              2        0     0         0       0   
99               1              1        0     0         0       0   

    absolutely  aca  access  accessibility  ...   bow_pc1    bow_pc2  \
0            0    0       0              0  ...  0.035800   0.476499   
1            0    0       0              0  ... -0.029318  -3.012366   
2            0    0       0              0  ... -0.415604   0.220952   
3            0    0       0              0  ... -0.616861   0.195662   
4            0    0       0              0  ... -3.192929   3.658640   
..         ...  ...     ...            ...  ...       ...        ...   
95           0    0       0              0  ... -0.363031   0.195922   
96           0    0       0              0  ... -0.720607  -1.372497   
97           0    0       0              0  ... -0.304784   2.598945   
98           0    0       0              0  ... -1.652893 -13.862187   
99           0    0       0              0  ... -0.558381  -0.275912   

      bow_pc3  bow_spec1  bow_spec2  bow_spec3   bow_tsne1   bow_tsne2  \
0   -0.454764   0.010146  -0.003825  -0.001798 -112.039619 -108.548744   
1    2.710507  -0.007385   0.038849  -0.025337  -99.995544  -37.590397   
2   -0.758795   0.010146  -0.003825  -0.001798   28.277555  -72.371971   
3   -0.846422  -0.015808  -0.010316  -0.004607   47.616013  134.119476   
4    0.605754  -0.015808  -0.010316  -0.004607  -51.282043  152.328903   
..        ...        ...        ...        ...         ...         ...   
95  -0.316556   0.000022   0.000108   0.000005    2.738613  -96.402504   
96  -2.908082  -0.015808  -0.010316  -0.004607  159.550186    4.630407   
97  -1.198380  -0.007385   0.038849  -0.025337    7.850263   40.945190   
98  54.323792   0.003989  -0.013730  -0.000523  -61.353710 -118.110573   
99  -0.064386  -0.015808  -0.010316  -0.004607  -79.225845  -86.646431   

     bow_tsne3    Year  
0    -7.316100  2017.0  
1  -116.876801  2020.0  
2   210.781052  2014.0  
3    22.153780  2017.0  
4    66.466370  2019.0  
..         ...     ...  
95   -8.666757  2019.0  
96   61.589588  2019.0  
97 -117.737854  2018.0  
98  -58.619637  2017.0  
99   64.854485  2016.0  

[100 rows x 2078 columns]

In [ ]:
elastic_net_classifier.fit(X_train, y_train)

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/s

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

...

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
/Users/nesli/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:

Maybe to ignore warnings 
#From  https://stackoverflow.com/questions/53784971/how-to-disable-convergencewarning-using-sklearn
@ignore_warnings(category=ConvergenceWarning)
def my_function():
    # Code that triggers the warning

In [ ]:
y_test=logistic_regression_classifier.predict(X_test)

In [ ]:
#add a numerical column for the class
y_test['party']=[0] * len(y_test)

for i in np.arange(len(y_test)):
    #Because D is the default
    if y_test['party'][i]==0:
        y_test['party'][i]='D'
    else:
        y_test['party'][i]='R'

In [ ]:
y_test.insert(0, "Id", X_test['Id'])

In [ ]:
y_test

In [ ]:
y_test.to_csv('submit_logreg_istanbul.csv')

## **References**

[1] https://www.analyticsvidhya.com/blog/2021/08/a-friendly-guide-to-nlp-bag-of-words-with-python-example/

[2] https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/

[3] https://stackoverflow.com/questions/40755680/how-to-reset-index-pandas-dataframe-after-dropna-pandas-dataframe

[4] https://stackoverflow.com/questions/28199524/best-way-to-count-the-number-of-rows-with-missing-values-in-a-pandas-dataframe

[5] https://stackoverflow.com/questions/66787845/how-to-perform-elastic-net-for-a-classification-problem